In [1]:
import json
import pandas as pd
import jieba
from jieba import posseg
import numpy as np
from loader import *
import torch
import sys
from modules import embedding, encoder, model_sbj
from sklearn.model_selection import KFold

In [11]:
file_path = '../data/train_data.json'
nums = 0
all_nums = 0
with open(file_path, 'r') as f:
    for line in f:
        all_nums += 1
        tmp = json.loads(line)
        spo_list = tmp['spo_list']
        so = [(spo['subject'], spo['object']) for spo in spo_list]
        if len(so) != len(set(so)):
            nums += 1
            print(spo_list)

[{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '王珂', 'subject': '狙击部队'}, {'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '赵浚凯', 'subject': '狙击部队'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '赵浚凯', 'subject': '狙击部队'}, {'predicate': '出品公司', 'object_type': '企业', 'subject_type': '影视作品', 'object': '海润', 'subject': '狙击部队'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '刘鑫', 'subject': '狙击部队'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '赵聪', 'subject': '狙击部队'}]
[{'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '周杰伦', 'subject': '龙卷风'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '周杰伦', 'subject': '龙卷风'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '周杰伦', 'subject': '告白气球'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '周杰伦', 'subject':

[{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '李悦宁', 'subject': '情同手足'}, {'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '李悦宁', 'subject': '情同手足'}]
[{'predicate': '出生地', 'object_type': '地点', 'subject_type': '人物', 'object': '德国', 'subject': '克维亚特科夫斯基'}, {'predicate': '国籍', 'object_type': '国家', 'subject_type': '人物', 'object': '德国', 'subject': '克维亚特科夫斯基'}]
[{'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '钟彩媚', 'subject': '宝贝回家'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '钟彩媚', 'subject': '幸福你我'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '钟彩媚', 'subject': '奶奶我爱你'}, {'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '钟彩媚', 'subject': '幸福你我'}]
[{'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '王晶', 'subject': '精装追女仔'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '周润发', 'sub

[{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '黄凯芹', 'subject': '难得糊涂'}, {'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '黄凯芹', 'subject': '难得糊涂'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '谭咏麟', 'subject': '难得糊涂'}]
[{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '肖顺尧', 'subject': '可惜不是你'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '范世錡', 'subject': '可惜不是你'}, {'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '叶紫', 'subject': '可惜不是你'}, {'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '叶紫', 'subject': '可惜不是你'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '宋妍霏', 'subject': '可惜不是你'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '英英鹿', 'subject': '可惜不是你'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '陈斯琪', 

[{'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '郭靖宇', 'subject': '铁梨花'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '巍子', 'subject': '铁梨花'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '杨志刚', 'subject': '铁梨花'}, {'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '郭靖宇', 'subject': '铁梨花'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '张少华', 'subject': '铁梨花'}, {'predicate': '出品公司', 'object_type': '企业', 'subject_type': '影视作品', 'object': '大连天歌传媒股份有限公司', 'subject': '铁梨花'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '陈数', 'subject': '铁梨花'}]
[{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '李峻一', 'subject': '坏孩子的天空'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '陈冠希', 'subject': '坏孩子的天空'}, {'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type': '歌曲', 'object': '

[{'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '王绎龙', 'subject': '累啊累'}, {'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '王绎龙', 'subject': '累啊累'}]
[{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '陈思诚', 'subject': '北京爱情故事'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '陈思诚', 'subject': '北京爱情故事'}]
[{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '陈绮贞', 'subject': '不应该'}, {'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '陈绮贞', 'subject': '不应该'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '陈绮贞', 'subject': '不应该'}]
[{'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '王子鸣', 'subject': '对你说'}, {'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type': '歌曲', 'object': '感觉爱情', 'subject': '对你说'}, {'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '仓雁彬', 'subject':

...

[{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '杰森·斯坦森', 'subject': '怒火攻心'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '布莱恩·泰勒', 'subject': '怒火攻心'}, {'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '布莱恩·泰勒', 'subject': '怒火攻心'}]
[{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '李聪', 'subject': '深梦'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '严艺丹', 'subject': '深梦'}, {'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '严艺丹', 'subject': '深梦'}]
[{'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '河森正治', 'subject': '创圣的大天使'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '河森正治', 'subject': '创圣的大天使'}]
[{'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '许冠杰', 'subject': '应该要自爱'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '许冠杰

[{'predicate': '上映时间', 'object_type': 'Date', 'subject_type': '影视作品', 'object': '2004年9月25日', 'subject': '奶油柠檬'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '根岸季衣', 'subject': '奶油柠檬'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '山下敦弘', 'subject': '奶油柠檬'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '山下敦弘', 'subject': '奶油柠檬'}]
[{'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '崔涛', 'subject': '肥猫瘦狗精灵鼠'}, {'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '崔涛', 'subject': '肥猫瘦狗精灵鼠'}]
[{'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': 'Jae', 'subject': '我会好好过'}, {'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type': '歌曲', 'object': 'baby是我', 'subject': '我会好好过'}, {'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '林燕岑', 'subject': '我会好好过'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': 

[{'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '陈晓娟', 'subject': '心不在焉'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '梁咏琪', 'subject': '心不在焉'}, {'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '陈晓娟', 'subject': '心不在焉'}]
[{'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '王杰', 'subject': '我唔讲粗口'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '王杰', 'subject': '我唔讲粗口'}, {'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type': '歌曲', 'object': '万岁2001', 'subject': '我唔讲粗口'}, {'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '林敏骢', 'subject': '我唔讲粗口'}]
[{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '毛晓彤', 'subject': '神雕侠侣'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '陈妍希', 'subject': '神雕侠侣'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '于正', 'su

[{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '袁攀', 'subject': '抵不过距离的爱'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '小娇', 'subject': '抵不过距离的爱'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '袁攀', 'subject': '抵不过距离的爱'}, {'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type': '歌曲', 'object': '依偎的故事', 'subject': '抵不过距离的爱'}, {'predicate': '作曲', 'object_type': '人物', 'subject_type': '歌曲', 'object': '袁攀', 'subject': '抵不过距离的爱'}]
[{'predicate': '出生地', 'object_type': '地点', 'subject_type': '人物', 'object': '韩国', 'subject': 'rain'}, {'predicate': '国籍', 'object_type': '国家', 'subject_type': '人物', 'object': '韩国', 'subject': 'rain'}]
[{'predicate': '主持人', 'object_type': '人物', 'subject_type': '电视综艺', 'object': 'Angelababy', 'subject': '奔跑吧兄弟'}, {'predicate': '嘉宾', 'object_type': '人物', 'subject_type': '电视综艺', 'object': 'Angelababy', 'subject': '奔跑吧兄弟'}]
[{'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [10]:
nums / all_nums

0.04342953531899161

In [9]:
all_nums

173108

In [3]:
a = gen_train_data_spo(file_path)

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.441 seconds.
Prefix dict has been built succesfully.


spo make samples, nums:191739/196864, radio:0.9740


In [5]:
for i_list in a[4]:
    for i in i_list:
        if i >= 50:
            print(i_list)

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 6.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 65.0, 0.0, 0.0, 0.0, 0.0, 23.0, 0.0, 0.0, 23.0, 0.0, 0.0, 23.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 23.0, 0.0, 0.0, 23.0, 0.0, 0.0, 0.0, 0.0, 0.0, 77.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 65.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 39.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 38.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 32.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 39.0, 0.0, 0.0, 0.0, 0.0, 0.0, 53.0, 0.0, 0.0, 5.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 77.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

[72.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 32.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 72.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.

In [25]:
    with open('../data/p_dict.pkl', 'rb') as f:
        i2s = pickle.load(f)

In [26]:
i2s

{'p2i': {'丈夫': 1,
  '歌手': 2,
  '占地面积': 3,
  '邮政编码': 4,
  '国籍': 5,
  '出品公司': 6,
  '出版社': 7,
  '注册资本': 8,
  '上映时间': 9,
  '民族': 10,
  '目': 11,
  '所在城市': 12,
  '创始人': 13,
  '成立日期': 14,
  '祖籍': 15,
  '导演': 16,
  '制片人': 17,
  '气候': 18,
  '修业年限': 19,
  '连载网站': 20,
  '主持人': 21,
  '父亲': 22,
  '主演': 23,
  '人口数量': 24,
  '总部地点': 25,
  '简称': 26,
  '作词': 27,
  '作者': 28,
  '首都': 29,
  '号': 30,
  '董事长': 31,
  '所属专辑': 32,
  '朝代': 33,
  '专业代码': 34,
  '毕业院校': 35,
  '嘉宾': 36,
  '海拔': 37,
  '出生地': 38,
  '出生日期': 39,
  '妻子': 40,
  '字': 41,
  '身高': 42,
  '作曲': 43,
  '主角': 44,
  '官方语言': 45,
  '面积': 46,
  '改编自': 47,
  '母亲': 48,
  '编剧': 49},
 'i2p': {1: '丈夫',
  2: '歌手',
  3: '占地面积',
  4: '邮政编码',
  5: '国籍',
  6: '出品公司',
  7: '出版社',
  8: '注册资本',
  9: '上映时间',
  10: '民族',
  11: '目',
  12: '所在城市',
  13: '创始人',
  14: '成立日期',
  15: '祖籍',
  16: '导演',
  17: '制片人',
  18: '气候',
  19: '修业年限',
  20: '连载网站',
  21: '主持人',
  22: '父亲',
  23: '主演',
  24: '人口数量',
  25: '总部地点',
  26: '简称',
  27: '作词',
  28: '作者',
  29: '首都',
  30: 

In [2]:
def gen_train_data_sbj(file_path):
    sbj_dict = get_type_dict_sbj()
    texts = []
    text_lists = []
    tag_lists = []
    spo_lists = []
    with open(file_path, 'r') as f:
        for line in f:
            tmp = json.loads(line)
            texts.append(tmp['text'])
            text_list, tag_list = list(zip(*posseg.lcut(tmp['text'], HMM=False)))
            text_list = list(text_list)
            tag_list = list(tag_list)
            text_lists.append(text_list)
            tag_lists.append(tag_list)
            spo_lists.append(tmp['spo_list'])

    with open('../data/sbj_dict.pkl', 'rb') as f:
        sbj2i = pickle.load(f)['sbj2i']

    r_text_lists = []
    r_tag_lists = []
    r_sbjs = []
    nums = 0
    for text_list, tag_list, spo_list in zip(text_lists, tag_lists, spo_lists):
        text_len = len(text_list)
        sbj = np.zeros(text_len)

        spo_extract = set()
        for spo in spo_list:
            sbj_list, _ = list(zip(*posseg.lcut(spo['subject'], HMM=False)))
            sbj_list = list(sbj_list)
            sbj_len = len(sbj_list)
            for i in range(0, text_len-sbj_len+1):
                if text_list[i: i+sbj_len] == sbj_list:
                    sbj_s = i
                    sbj_e = i + sbj_len - 1
                    xxx = sbj_dict[spo['subject_type']]
                    if sbj_s == sbj_e:
                        sbj[sbj_s] = sbj2i[xxx]
                    elif sbj_e - sbj_s == 1:
                        sbj[sbj_s] = sbj2i[xxx]
                        sbj[sbj_e] = sbj2i[xxx] + 2
                    elif sbj_e - sbj_s > 1:
                        sbj[sbj_s] = sbj2i[xxx]
                        sbj[sbj_s+1: sbj_e] = sbj2i[xxx] + 1
                        sbj[sbj_e] = sbj2i[xxx] + 2
                    else:
                        print('wrong')
                        assert 1 == -1
                    spo_extract.add(spo['subject'])
        nums += len(spo_extract)
        if len(spo_extract) != 0:
            r_text_lists.append(text_list)
            r_tag_lists.append(tag_list)
            r_sbjs.append(sbj.tolist())

    all_nums = 0
    for spo_list in spo_lists:
        all_nums += len(set([spo['subject'] for spo in spo_list]))

    print('sbj, make samples_num:%d, sbj_nums:%d/%d, radio:%.4f' % (len(r_text_lists), nums, all_nums, nums/all_nums))

    return r_text_lists, r_tag_lists, r_sbjs

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.449 seconds.
Prefix dict has been built succesfully.


sbj, make samples_num:172333, sbj_nums:195042/196864, radio:0.9907


In [37]:
'a[2][23]我靠dsaAS'.lower()

'a[2][23]我靠dsaas'

In [35]:
spo_lists = spo_list
all_nums = 0
for spo_list in spo_lists:
    all_nums += len([spo['subject'] for spo in spo_list])

print('sbj, make samples_num:%d, sbj_nums:%d/%d, radio:%.4f' % (len(texts), nums, all_nums, nums/all_nums))

sbj, make samples_num:173109, sbj_nums:361242/364218, radio:0.9918


In [ ]:
words = [jieba.lcut(item['word'], HMM=False) for item in tmp['postag']]